In [1]:
from bertopic import BERTopic
import pandas as pd
from sklearn.metrics.pairwise import cosine_similarity
from opensearch_data_model import Topic, TopicKeyword, os_client
from datetime import datetime
from dateutil.parser import parse
from utils import SPANISH_STOPWORDS
from bertopic import BERTopic
from umap import UMAP
from hdbscan import HDBSCAN
from sklearn.cluster import DBSCAN
from sentence_transformers import SentenceTransformer
from sklearn.feature_extraction.text import CountVectorizer
from bertopic.representation import KeyBERTInspired
from bertopic.vectorizers import ClassTfidfTransformer
from sklearn.metrics import silhouette_score
import numpy as np

c:\Users\gaspa\anaconda3\envs\topics\Lib\site-packages\urllib3\connectionpool.py:1063: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(


In [2]:
import pandas as pd
df = pd.read_parquet('data\df_joined_2024-04-01 00_00_00.paquet')

In [3]:
df['out__keywords_sorted']

Asset Id
105628101    [elecciones presidenciales, candidatura presid...
105628367    [suficiente ahorro interno, descomunal tasa, d...
105629611    [cuadros difíciles, secuelas, palabra trauma, ...
105629617    [generación, billetes, revolución, tarjetas, b...
105628730    [galante gesto, generosidad, amigos, mesa comp...
                                   ...                        
105641179    [impuestos, tasas, hotel, entrada, paquetes im...
105593608                 [golpe, excesos, acto, jefe, tiempo]
105580130    [ventas, unidades, caída, rentabilidad, comerc...
105640664    [héroes, fuerzas armadas, reconciliación, diri...
105580630    [estación facultad, remodelación integral, sub...
Name: out__keywords_sorted, Length: 3104, dtype: object

In [3]:
df['in__title']

Asset Id
105628101    Elecciones en Venezuela: María Corina Machado ...
105628367    El populismo derivó en que los argentinos fina...
105629611    Día de los veteranos de Malvinas: el impacto y...
105629617    La revolución del efectivo: la Generación Z re...
105628730    El galante gesto de Diego Maradona con Mariana...
                                   ...                        
105641179    Cuánto cuesta ver a la Selección Argentina en ...
105593608    Javier Milei contra Estela de Carlotto: "Pidió...
105580130    Comercios en Córdoba: cayó 20.9% las ventas po...
105640664    Milei homenajeó a los héroes de Malvinas y con...
105580630    Subtes: reabrió la estación Facultad de Medici...
Name: in__title, Length: 3104, dtype: object

In [4]:
df['in__text']

Asset Id
105628101    Fotografía de archivo de la líder antichavista...
105628367    El argentino sabe que su moneda de ahorro es e...
105629611    El trauma es una respuesta emocional a un even...
105629617    La vuelta al efectivo es tendencia entre los C...
105628730    Diego Maradona tuvo un generoso gesto para con...
                                   ...                        
105641179    Copa América 2024\n\nLa Selección Argentina di...
105593608    Durante la entrevista que el jefe de Estado co...
105580130    La Cámara de Comercio de Córdoba informó la ca...
105640664    Con un mensaje con marcado tono político y eco...
105580630    A partir de hoy, la línea D volvió a funcionar...
Name: in__text, Length: 3104, dtype: object

In [3]:
title_text = [f"{title}. {doc}" for title, doc in zip(df['in__title'], df['in__text'])]

In [33]:
title_text

['Elecciones en Venezuela: María Corina Machado pidió más apoyo de Noruega para garantizar unas presidenciales libres. Fotografía de archivo de la líder antichavista María Corina Machado (EFE/ Rayner Peña R.)\n\nLa líder opositora María Corina Machado pidió a Noruega -país mediador en las negociaciones entre el régimen de Venezuela y la oposición mayoritaria- extremar su apoyo para garantizar que en el país caribeño se celebren, el próximo 28 de julio, unas presidenciales “libres y justas”, según una comunicación difundida este lunes, que insta a que presione al dictador Nicolás Maduro para que cumpla con el Acuerdo de Barbados y admita la candidatura presidencial de su sucesora, Corina Yoris.\n\nLa carta, dirigida al primer ministro noruego, Jonas Gahr, tiene el objetivo de exhortar a su Gobierno, en “su calidad de facilitador del proceso de diálogo y negociación entre actores políticos de Venezuela, a extremar los recursos diplomáticos a su disposición” para que el acuerdo de Barbado

## fist model

In [40]:
topic_model = BERTopic(language='Spanish')

In [41]:
topics, probs = topic_model.fit_transform(title_text)

In [42]:
topic_model.get_topic_info()

Topic  Count                                     Name  \
0      -1    784                          -1_de_que_la_en   
1       0    100           0_malvinas_caídos_guerra_milei   
2       1     82      1_semana_ocupación_turismo_turistas   
3       2     73       2_dengue_mosquitos_wolbachia_casos   
4       3     61       3_uncuyo_coro_plena_interpretación   
..    ...    ...                                      ...   
83     82     11         82_cáncer_kate_doherty_middleton   
84     83     11               83_akins_malvinas_me_lanús   
85     84     11  84_documental_kreplak_película_pandemia   
86     85     10         85_pami_medicamentos_ác_arterial   
87     86     10           86_tope_dni_consumos_comercios   

                                       Representation  \
0      [de, que, la, en, el, los, con, un, para, las]   
1   [malvinas, caídos, guerra, milei, villarruel, ...   
2   [semana, ocupación, turismo, turistas, fin, de...   
3   [dengue, mosquitos, wolbachia, casos, mosquito...   
4   [uncuyo, coro, plena, interpretación, cámara, ...   
..                                                ...   
83  [cáncer, kate, doherty, middleton, garner, pri...   
84  [akins, malvinas, me, lanús, era, fue, inglese...   
85  [documental, kreplak, película, pandemia, salu...   
86  [pami, medicamentos, ác, arterial, hipertensió...   
87  [tope, dni, consumos, comercios, cuenta, alcan...   

                                  Representative_Docs  
0   [Adelanto exclusivo del libro de Marcos Peña: ...  
1   [Javier Milei rindió homenaje a los caídos a 4...  
2   [El destino del país que tuvo récord histórico...  
3   [Wolbachia: el método innovador con el que Col...  
4   [Víctor Hugo Vieyra: los teatros que construyó...  
..                                                ...  
83  [Shannen Doherty contó cómo se prepara para mo...  
84  ["Un 1° de abril desembarcó en Malvinas y otro...  
85  ["Goebbels estaría orgulloso": el PRO pide sab...  
86  [Los medicamentos gratis que están disponibles...  
87  [CUENTA DNI: uno por uno, TODOS los DESCUENTOS...  

[88 rows x 5 columns]

In [43]:
topic_model.visualize_heatmap()

In [44]:
embeddings = topic_model.embedding_model.embed(title_text)

# Filter out documents with no assigned topic (-1)
valid_indices = [i for i, topic in enumerate(topics) if topic != -1]
valid_embeddings = [embeddings[i] for i in valid_indices]
valid_topics = [topics[i] for i in valid_indices]

# Calculate the silhouette score
silhouette_score(valid_embeddings, valid_topics,metric='cosine')

0.1982859

## second model

In [45]:
embedding_model = SentenceTransformer('paraphrase-multilingual-MiniLM-L12-v2') 

In [46]:
tf_vectorizer = CountVectorizer(
    ngram_range=(1, 2),
    stop_words=SPANISH_STOPWORDS,
    lowercase=True,
)

In [47]:
#umap_model = UMAP(n_neighbors=15, n_components=5, min_dist=0.0, metric='cosine')

In [48]:
ctfidf_model = ClassTfidfTransformer()

In [49]:
#hdbscan_model = HDBSCAN(min_cluster_size=30, metric='euclidean', cluster_selection_method='eom', prediction_data=True)

In [50]:
topic_model = BERTopic(language='Spanish',embedding_model=embedding_model,vectorizer_model=tf_vectorizer,ctfidf_model=ctfidf_model)

In [51]:
topics, probs = topic_model.fit_transform(title_text)

In [52]:
topic_model.get_topic_info()

Topic  Count                                         Name  \
0      -1    751                -1_alcohol_años_radar_consumo   
1       0    110     0_malvinas_guerra_caídos_guerra malvinas   
2       1     86  1_radioinforme_rosario_mañana mañana_cadena   
3       2     81          2_semana_ocupación_turismo_turistas   
4       3     73           3_dengue_mosquitos_wolbachia_casos   
..    ...    ...                                          ...   
81     80     11      80_documental_kreplak_película_pandemia   
82     81     11                       81_gtx_buzz_id buzz_id   
83     82     11           82_autismo_médula_médula ósea_ósea   
84     83     11                     83_inter_empoli_serie_30   
85     84     10        84_francos_gobernadores_ley_ley bases   

                                       Representation  \
0   [alcohol, años, radar, consumo, cerebro, foto,...   
1   [malvinas, guerra, caídos, guerra malvinas, vi...   
2   [radioinforme, rosario, mañana mañana, cadena,...   
3   [semana, ocupación, turismo, turistas, semana ...   
4   [dengue, mosquitos, wolbachia, casos, mosquito...   
..                                                ...   
81  [documental, kreplak, película, pandemia, salu...   
82  [gtx, buzz, id buzz, id, diseño, buzz gtx, toy...   
83  [autismo, médula, médula ósea, ósea, donantes,...   
84  [inter, empoli, serie, 30, 29, dimarco, lautar...   
85  [francos, gobernadores, ley, ley bases, bases,...   

                                  Representative_Docs  
0   [Adelanto exclusivo del libro de Marcos Peña: ...  
1   [Javier Milei rindió homenaje a los caídos a 4...  
2   [Murió de dengue la esposa del golfista argent...  
3   [Turismo en Córdoba: sorpresa por un movimient...  
4   [Wolbachia: el método innovador con el que Col...  
..                                                ...  
81  [El PRO pide saber quién financió el documenta...  
82  [El viejo y popular calibre 22 LR. El .22 es e...  
83  [Día del Donante de Médula Ósea: ¿en qué consi...  
84  [El Inter de Lautaro Martínez venció a Empoli ...  
85  [Guillermo Francos negocia con los gobernadore...  

[86 rows x 5 columns]

In [53]:
topic_model.visualize_heatmap()

In [54]:
embeddings = topic_model.embedding_model.embed(title_text)

# Filter out documents with no assigned topic (-1)
valid_indices = [i for i, topic in enumerate(topics) if topic != -1]
valid_embeddings = [embeddings[i] for i in valid_indices]
valid_topics = [topics[i] for i in valid_indices]

# Calculate the silhouette score
silhouette_score(valid_embeddings, valid_topics,metric='cosine')

0.20598489

## third model

In [55]:
embedding_model = SentenceTransformer('paraphrase-multilingual-MiniLM-L12-v2') 

In [56]:
tf_vectorizer = CountVectorizer(
    ngram_range=(1, 2),
    stop_words=SPANISH_STOPWORDS,
    lowercase=True,
)

In [57]:
umap_model = UMAP(n_neighbors=15, n_components=20, min_dist=0.0, metric='cosine')

In [58]:
ctfidf_model = ClassTfidfTransformer()

In [59]:
#hdbscan_model = HDBSCAN(min_cluster_size=30, metric='euclidean', cluster_selection_method='eom', prediction_data=True)

In [60]:
topic_model = BERTopic(language='Spanish',embedding_model=embedding_model,umap_model=umap_model,vectorizer_model=tf_vectorizer,ctfidf_model=ctfidf_model)

In [61]:
topics, probs = topic_model.fit_transform(title_text)

In [62]:
topic_model.get_topic_info()

Topic  Count                                         Name  \
0      -1    807                -1_alcohol_años_radar_consumo   
1       0    111     0_malvinas_guerra_caídos_guerra malvinas   
2       1     88          1_semana_ocupación_turismo_turistas   
3       2     85  2_radioinforme_rosario_mañana mañana_cadena   
4       3     73           3_dengue_mosquitos_wolbachia_casos   
..    ...    ...                                          ...   
77     76     11                       76_gtx_id buzz_buzz_id   
78     77     11            77_shakira_mujeres_barbie_hombres   
79     78     11           78_racing_olave_nasta_carlos olave   
80     79     11      79_documental_kreplak_película_pandemia   
81     80     10         80_belgrano_inter_porto alegre_porto   

                                       Representation  \
0   [alcohol, años, radar, consumo, foto, cerebro,...   
1   [malvinas, guerra, caídos, guerra malvinas, mi...   
2   [semana, ocupación, turismo, turistas, semana ...   
3   [radioinforme, rosario, mañana mañana, cadena,...   
4   [dengue, mosquitos, wolbachia, casos, mosquito...   
..                                                ...   
77  [gtx, id buzz, buzz, id, diseño, buzz gtx, toy...   
78  [shakira, mujeres, barbie, hombres, katy perry...   
79  [racing, olave, nasta, carlos olave, juan carl...   
80  [documental, kreplak, película, pandemia, salu...   
81  [belgrano, inter, porto alegre, porto, alegre,...   

                                  Representative_Docs  
0   [Inter vs. Empoli, por la Serie A: horario, fo...  
1   [Javier Milei rindió homenaje a los caídos a 4...  
2   [Turismo en Córdoba: sorpresa por un movimient...  
3   [Murió de dengue la esposa del golfista argent...  
4   [Wolbachia: el método innovador con el que Col...  
..                                                ...  
77  [El viejo y popular calibre 22 LR. El .22 es e...  
78  [Qué dijo Shakira sobre la película Barbie y p...  
79  [Nasta, Bustos y Oyola fueron los puntos más a...  
80  [El PRO pide saber quién financió el documenta...  
81  [La lista de Belgrano para su debut internacio...  

[82 rows x 5 columns]

In [63]:
topic_model.visualize_heatmap()

In [64]:
embeddings = topic_model.embedding_model.embed(title_text)

# Filter out documents with no assigned topic (-1)
valid_indices = [i for i, topic in enumerate(topics) if topic != -1]
valid_embeddings = [embeddings[i] for i in valid_indices]
valid_topics = [topics[i] for i in valid_indices]

# Calculate the silhouette score
silhouette_score(valid_embeddings, valid_topics,metric='cosine')

0.21174876

## fourth model

In [4]:
embedding_model = SentenceTransformer('paraphrase-multilingual-MiniLM-L12-v2') 

In [5]:
tf_vectorizer = CountVectorizer(
    ngram_range=(1, 2),
    stop_words=SPANISH_STOPWORDS,
    lowercase=True,
)

In [6]:
umap_model = UMAP(n_neighbors=15, n_components=20, min_dist=0.0, metric='cosine')

In [7]:
ctfidf_model = ClassTfidfTransformer()

In [8]:
hdbscan_model = HDBSCAN(min_cluster_size=10, metric='euclidean', cluster_selection_method='eom', prediction_data=True)

In [9]:
topic_model = BERTopic(language='Spanish',embedding_model=embedding_model,umap_model=umap_model,hdbscan_model=hdbscan_model,vectorizer_model=tf_vectorizer,ctfidf_model=ctfidf_model)

In [10]:
topics, probs = topic_model.fit_transform(title_text)

In [11]:
df['topic'] = topics

In [37]:
topic_model.get_topic_info()

Topic  Count                                         Name  \
0      -1    852                -1_alcohol_años_radar_consumo   
1       0    102     0_malvinas_caídos_guerra_guerra malvinas   
2       1     85  1_radioinforme_rosario_mañana mañana_cadena   
3       2     82          2_semana_ocupación_turismo_turistas   
4       3     73           3_dengue_mosquitos_wolbachia_casos   
..    ...    ...                                          ...   
76     75     11                       75_gtx_id buzz_buzz_id   
77     76     11             76_akins_malvinas_lanús_ingleses   
78     77     11               77_malvinas_guerra_islas_museo   
79     78     11      78_documental_kreplak_película_pandemia   
80     79     11               79_tope_dni_consumos_comercios   

                                       Representation  \
0   [alcohol, años, radar, consumo, foto, día, cer...   
1   [malvinas, caídos, guerra, guerra malvinas, vi...   
2   [radioinforme, rosario, mañana mañana, cadena,...   
3   [semana, ocupación, turismo, turistas, semana ...   
4   [dengue, mosquitos, wolbachia, casos, mosquito...   
..                                                ...   
76  [gtx, id buzz, buzz, id, diseño, buzz gtx, toy...   
77  [akins, malvinas, lanús, ingleses, brian, reti...   
78  [malvinas, guerra, islas, museo, 1982, argenti...   
79  [documental, kreplak, película, pandemia, salu...   
80  [tope, dni, consumos, comercios, banco provinc...   

                                  Representative_Docs  
0   [Un estafador nos engañó por Facebook Marketpl...  
1   [Javier Milei rindió homenaje a los caídos a 4...  
2   [Murió de dengue la esposa del golfista argent...  
3   [Turismo en Córdoba: sorpresa por un movimient...  
4   [Wolbachia: el método innovador con el que Col...  
..                                                ...  
76  [El viejo y popular calibre 22 LR. El .22 es e...  
77  [Fue compañero de Insua en San Lorenzo, jugó e...  
78  [El impacto de la Guerra de Malvinas en el roc...  
79  [El PRO pide saber quién financió el documenta...  
80  [CUENTA DNI: uno por uno, TODOS los DESCUENTOS...  

[81 rows x 5 columns]

In [38]:
topic_model.visualize_heatmap()

In [39]:
embeddings = topic_model.embedding_model.embed(title_text)

# Filter out documents with no assigned topic (-1)
valid_indices = [i for i, topic in enumerate(topics) if topic != -1]
valid_embeddings = [embeddings[i] for i in valid_indices]
valid_topics = [topics[i] for i in valid_indices]

# Calculate the silhouette score
silhouette_score(valid_embeddings, valid_topics,metric='cosine')

0.21604657

## SUMMARIZING

In [19]:
from summarizer import Summarizer

# Input text to be summarized
input_text = f"""
{title_text[0]} 
"""

# Create a BERT extractive summarizer
summarizer = Summarizer()

# Generate the summary
summary = summarizer(input_text, min_length=50, max_length=150)  # You can adjust the min_length and max_length parameters

# Output the summary
print("Original Text:")
print(input_text)
print("\nSummary:")
print(summary)

Original Text:

Elecciones en Venezuela: María Corina Machado pidió más apoyo de Noruega para garantizar unas presidenciales libres. Fotografía de archivo de la líder antichavista María Corina Machado (EFE/ Rayner Peña R.)

La líder opositora María Corina Machado pidió a Noruega -país mediador en las negociaciones entre el régimen de Venezuela y la oposición mayoritaria- extremar su apoyo para garantizar que en el país caribeño se celebren, el próximo 28 de julio, unas presidenciales “libres y justas”, según una comunicación difundida este lunes, que insta a que presione al dictador Nicolás Maduro para que cumpla con el Acuerdo de Barbados y admita la candidatura presidencial de su sucesora, Corina Yoris.

La carta, dirigida al primer ministro noruego, Jonas Gahr, tiene el objetivo de exhortar a su Gobierno, en “su calidad de facilitador del proceso de diálogo y negociación entre actores políticos de Venezuela, a extremar los recursos diplomáticos a su disposición” para que el acuerdo 

In [12]:
from transformers import T5Tokenizer, T5ForConditionalGeneration

# Load pre-trained T5 model and tokenizer
model_name = "google-t5/t5-large"
tokenizer = T5Tokenizer.from_pretrained(model_name)
model = T5ForConditionalGeneration.from_pretrained(model_name)

# Input text to be summarized
input_text = f"""
{title_text[0]} 
"""

# Tokenize and summarize the input text using T5
inputs = tokenizer.encode("summarize: " + input_text, return_tensors="pt", max_length=1024, truncation=True)
summary_ids = model.generate(inputs, max_length=20, min_length=10, length_penalty=2.0, num_beams=4, early_stopping=True)

# Decode and output the summary
summary = tokenizer.decode(summary_ids[0], skip_special_tokens=True)
print("Original Text:")
print(input_text)
print("\nSummary:")
print(summary)

You are using the default legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thoroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Original Text:

Elecciones en Venezuela: María Corina Machado pidió más apoyo de Noruega para garantizar unas presidenciales libres. Fotografía de archivo de la líder antichavista María Corina Machado (EFE/ Rayner Peña R.)

La líder opositora María Corina Machado pidió a Noruega -país mediador en las negociaciones entre el régimen de Venezuela y la oposición mayoritaria- extremar su apoyo para garantizar que en el país caribeño se celebren, el próximo 28 de julio, unas presidenciales “libres y justas”, según una comunicación difundida este lunes, que insta a que presione al dictador Nicolás Maduro para que cumpla con el Acuerdo de Barbados y admita la candidatura presidencial de su sucesora, Corina Yoris.

La carta, dirigida al primer ministro noruego, Jonas Gahr, tiene el objetivo de exhortar a su Gobierno, en “su calidad de facilitador del proceso de diálogo y negociación entre actores políticos de Venezuela, a extremar los recursos diplomáticos a su disposición” para que el acuerdo 

In [23]:
df_titles_by_topic=pd.DataFrame(columns=['topic','title'])
for i,f in enumerate(np.arange(df.topic.values.max()+1)):
    df_titles_by_topic = pd.concat([df_titles_by_topic,pd.DataFrame({'topic':[i],'title':[' '.join(df[df['topic']==i]['in__title'].values.astype(str))]})],ignore_index=True)
df_titles_by_topic


topic                                              title
0      0  Día de los veteranos de Malvinas: el impacto y...
1      1  Los desafíos para el turismo en 2024 Fin de se...
2      2  El Gobierno reveló cuál sería el piso mínimo d...
3      3  A qué temperatura puede sobrevivir el mosquito...
4      4  Murió la escritora Maryse Condé, activista con...
..   ...                                                ...
76    76  Este es el Toyota Corolla más económico del me...
77    77  Fue compañero de Insua en San Lorenzo, jugó en...
78    78  Un niño de 12 años mató a un compañero de clas...
79    79  Cuenta DNI: cuál será el gran beneficio que te...
80    80  Instagram permite editar los mensajes directos...

[81 rows x 2 columns]

In [94]:
summaries = []
for i in df_titles_by_topic.title[:10]:
    input_text = f"""
    {i} 
    """

    # Tokenize and summarize the input text using T5
    inputs = tokenizer.encode("summarize: " + input_text, return_tensors="pt", max_length=2048, truncation=True)
    summary_ids = model.generate(inputs, max_length=30, min_length=10, length_penalty=2.0, num_beams=4, early_stopping=True)

    # Decode and output the summary
    summaries.append(tokenizer.decode(summary_ids[0], skip_special_tokens=True))
summaries


['Milei y Villarruel encabezarán el acto central por el 42o ani',
 'Termas de Ro Hondo fue uno de los destinos más elegidos por los',
 'Atlético Tucumán empató con Independiente Rivadavia en el estadio de',
 'el Gobierno reveló cuál sera el piso mnimo de',
 'lousteau criticó a javier milei por la falta de repelentes para combatir el dengue',
 'Malvinas es un programa imperdible para los amantes de la historia - MDZ Online',
 'Quién se va de Gran Hermano este lunes? Quén se va de Gran Her',
 'murió de dengue la esposa del golfista argentino Emilio Domnguez',
 'Israel bombardea el consulado de Irán en la capital de Siria y mató a',
 'Boca Juniors enfrentará a Nacional Potos por la fecha 1 del grup']

## SAVING TO OPENSEARCH

In [13]:
#Topic.init()

In [14]:
def get_topic_summary(topic_index):
    df_titles_by_topic=pd.DataFrame(columns=['topic','title'])
    df_titles_by_topic = pd.DataFrame({'topic':[topic_index],'title':[' '.join(df[df['topic']==topic_index]['in__title'].values.astype(str))]})
    inputs = tokenizer.encode("summarize: " + df_titles_by_topic['title'].values[0], return_tensors="pt", max_length=4096, truncation=True)
    summary_ids = model.generate(inputs, max_length=30, min_length=10, length_penalty=2.0, num_beams=4, early_stopping=True)

    # Decode and output the summary
    return tokenizer.decode(summary_ids[0], skip_special_tokens=True)

def get_entities(topic_index):
    entities = []
    for i in df[df['topic']==topic_index]['out__entities'].values:
            for n in i.tolist():
                if n not in entities:
                    entities.append(n)
    return entities
def get_keywords(topic_index):
    keywords_topic=[]
    for i in df[df['topic']==topic_index]['out__keywords_sorted'].values:
        for n in i.tolist():
            if n not in keywords_topic:
                keywords_topic.append(n)
    return keywords_topic


In [63]:
df_titles_by_topic=pd.DataFrame(columns=['topic','title'])
df_titles_by_topic = pd.DataFrame({'topic':[topic_index],'title':[' '.join(df[df['topic']==0]['in__title'].values.astype(str))]})
inputs = tokenizer.encode("summarize: " + df_titles_by_topic['title'].values[0], return_tensors="pt", max_length=4096, truncation=True)
summary_ids = model.generate(inputs, max_length=30, min_length=10, length_penalty=2.0, num_beams=4, early_stopping=True)
# Decode and output the summary
tokenizer.decode(summary_ids[0], skip_special_tokens=True)

'el jugador del Chelsea acusado de racismo por negarle a un n'

In [15]:

for topic_index in topic_model.get_topics().keys():
    if topic_index > -1:
        print(topic_index)

        topic_doc = Topic(
            vector = list(topic_model.topic_embeddings_[topic_index + 1]),
            similarity_threshold = 0.7,
            created_at = datetime.now(),
            to_date = parse('2024-04-02'),
            from_date = parse('2024-04-01'),
            index = topic_index,
            keywords = get_keywords(topic_index),
            name = get_topic_summary(topic_index),
            entities = get_entities(topic_index)
        )

        print(topic_doc.save())

0


c:\Users\gaspa\anaconda3\envs\topics\Lib\site-packages\urllib3\connectionpool.py:1063: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(


created
1


c:\Users\gaspa\anaconda3\envs\topics\Lib\site-packages\urllib3\connectionpool.py:1063: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(


created
2


...

c:\Users\gaspa\anaconda3\envs\topics\Lib\site-packages\urllib3\connectionpool.py:1063: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(


created
80


c:\Users\gaspa\anaconda3\envs\topics\Lib\site-packages\urllib3\connectionpool.py:1063: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(


created
81
created


c:\Users\gaspa\anaconda3\envs\topics\Lib\site-packages\urllib3\connectionpool.py:1063: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(


In [20]:
query = {
    "query": {
        "match": {
            "index": 1
        }
    }
}
response = os_client.search(index='topic', body=query)
response['hits']['hits']

c:\Users\gaspa\anaconda3\envs\topics\Lib\site-packages\urllib3\connectionpool.py:1063: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(


[{'_index': 'topic',
  '_id': '1el_Gobierno_reveló_cuál_sera_el_piso_mnimo_de',
  '_score': 1.0,
  '_source': {'vector': [-0.0018602238269522786,
    -0.04157790541648865,
    0.16683030128479004,
    0.07006902992725372,
    0.14788538217544556,
    -0.030180199071764946,
    0.09505248069763184,
    0.05930890515446663,
    0.061739519238471985,
    0.05373938009142876,
    0.23573312163352966,
    -0.18691150844097137,
    -0.14112907648086548,
    0.136146679520607,
    0.12359476834535599,
    -0.02890692837536335,
    -0.110727459192276,
    0.13258066773414612,
    0.01717991568148136,
    0.06841173022985458,
    0.2565661370754242,
    -0.04077785089612007,
    -0.04091687873005867,
    0.03274030610918999,
    -0.08480954170227051,
    0.15301582217216492,
    -0.07872530817985535,
    0.03946664184331894,
    -0.14695067703723907,
    -0.12029219418764114,
    -0.06205771490931511,
    0.10571129620075226,
    0.22464929521083832,
    0.12352745980024338,
    0.0463676638901

In [21]:
response['hits']['hits'][0]['_source']['name']

'el Gobierno reveló cuál sera el piso mnimo de'

In [22]:
response['hits']['hits'][0]['_source']['entities']

['Cadena 3 Argentina',
 'Pablo Sirvén',
 'Sergio Suppo',
 'Fernando Genesir',
 'Guillermo Francos',
 'Luis Caputo',
 'Claudio Vidal',
 'Mariano Pérez',
 'Alejandra Conti',
 'Patricia Bullrich',
 'Luis Petri',
 'Victoria Villarruel',
 'Rodolfo Barili',
 'Instagram',
 'Editorial Planeta',
 'Amazon Prime Video',
 'Guillermo López',
 'Flavio Mendoza',
 'Circo del Anima',
 'Waldo Wolff',
 'Juan Federico',
 'Instituto Nacional de la Yerba Mate',
 'Javier Milei',
 'Papa Francisco',
 'Juan José Campanella',
 'Perfil',
 'Ingeniería sin Fronteras',
 'Leandro Santoro',
 'Alberto Fernández',
 'Diario Jornada',
 'Agencia Córdoba Turismo',
 'La Cumbre',
 'Potrero de Garay',
 'Club Atlético River Plate',
 'Club Estudiantes de La Plata',
 'El Turista',
 'Luis Miguel',
 'Jorge Lanata',
 'CNN',
 'Morgan Stanley',
 'Mauricio Macri',
 'Nicolás Maduro',
 'Diana Mondino',
 'Fondo Monetario Internacional',
 'Noticias Argentinas',
 'Guillermo Moreno',
 'Cámara de Comercio de Córdoba',
 'Universidad de Palermo

In [23]:
response['hits']['hits'][0]['_source']['keywords']

['rosario',
 'radio',
 'código embebido',
 'deportes',
 'ganancias',
 'cuarta categoría',
 'pago retroactivo',
 'obligación',
 'tributo',
 'interés',
 'cadena',
 'piso mínimo',
 'turno',
 'opinión',
 'ministro',
 'café',
 'noche',
 'gobierno nacional',
 'impuesto anual',
 'números exactos',
 'ofrenda floral',
 'esquina',
 'cuadrado',
 'dato',
 'escalas',
 'tema',
 'regreso',
 'emisora',
 'retenciones',
 'conti',
 'solidaridad',
 'gesto',
 'nación',
 'talleres',
 'bases',
 'decreto',
 'mujer',
 'mercados',
 'mirada',
 'coagulación',
 'mesa',
 'foto',
 'guerra',
 'cupón',
 'educación',
 'funcionario',
 'declaraciones',
 'emisoras',
 'tesoros',
 'velorio',
 'gestión',
 'noticias',
 'país',
 'apropiación',
 'vigilia',
 'prescripción',
 'facturación',
 'salud',
 'religión',
 'conmoción',
 'islas',
 'amantes',
 'mandatarios',
 'capítulos',
 'vacuna',
 'canchas',
 'años',
 'situación',
 'presidente',
 'medicamentos',
 'disminución significativa',
 'variedad',
 'caso',
 'sanción',
 'foco',
 'f

In [19]:
import joblib
joblib.dump(topic_model,'topic_model')

['topic_model']